# TP3 : Levés TDEM

### Instructions pour le devoir

Ce laboratoire porte sur le traitement des mesures TDEM. Il porte plus particulièrement sur l'inversion et l'interprétation des données, et ne comporte pas de composante acquisition.
    
- Remplissez vos réponses dans les cellules indiquées. Les réponses peuvent prendre la forme d'un segment de code ou d'une réponses textuelle, ou les deux.
- Bien commenter les cellules de code afin de décrire la démarche.
- Assurez-vous que chaque cellule s'exécute et donne la réponse désirée avant de remettre votre notebook. Pour ce faire, il est recommandé d'exécuter Kernel -> Restart and Run All.
- Vous devez remettre les fichiers du jupyter notebook complété (.ipynb), ainsi que sa version pdf (File->Download as -> pdf).
- Ce travail doit être fait de façon individuelle, chaque personne doit remettre sa propre copie.


In [ ]:
%matplotlib inline
import warnings
warnings.filterwarnings('ignore')
import numpy as np
import matplotlib.pyplot as plt
import os
from FonctionTP3 import Modelisation_NanoTEM, Modelisation_VTEM, Inversion_VTEM, Inversion_NanoTEM
import matplotlib.patches as patches

## Introduction (Mise en contexte)

<p style="line-height:1.7 ; text-align: justify ">
La compagnie Hydro-Géophy Ltd. a acquis des données électromagnétiques transitoires (TDEM) pour imager le toit des eaux saumâtres laissées par la mer de Champlain dans le roc en Montérégie, dans les environs de Sorel. La stratigraphie attendue dans la région est résumée au tableau suivant.
    
\begin{array}{|c|c|c|c|}
\hline \textrm{Unité} & \textrm{Milieu} &  Épaisseur (m)& \rho \hspace{1mm} (\Omega\hspace{1mm}m) \\\hline
  \hspace{2cm} 1 \hspace{2cm}  & \hspace{2cm} \text{Sable saturé} \hspace{2cm} & \hspace{2cm} 15 \hspace{2cm} & \hspace{2cm} 30 \hspace{2cm} \\\hline
  2 &  \textrm{Argiles marines} & 25 & 5 \\\hline
  3 & \textrm{Calcaire} & 70 & 100 \\\hline
  4 & \textrm{Eaux saumâtres} & - & 15 \\\hline
\end{array}
</p>

<p style="line-height:1.7 ; text-align: justify ">
Cependant, certains des sondages réalisés sont de mauvaises qualités car ayant été affectés par la présence des lignes à haute tension. En prélude à une nouvelle campagne d’acquisition dont le but est d’obtenir des données de meilleure qualité, on vous demande de modéliser et d’inverser les courbes $\large \frac{\partial B_z}{\partial t} $ calculées à partir d’un modèle synthétique pour deux systèmes d’acquisition, le VTEM-plus et le NanoTEM, afin de proposer le système qui pourrait permettre de mieux imager le toit des eaux saumâtres. </p>

### Étape 1: Formulation du problème (0,25 points)

Quels sont les objectifs du levé géophysique ?

<span style="color:red">
Réponse:

</span>

### Étape 2: Choix des propriétés géophysiques (0,25 points)

Justifiez le choix d'une méthode sensible aux changements de résistivité électrique afin d'atteindre les objectifs du levé.

<span style="color:red">
Réponse:

</span>

### Étape 3: Choix de la méthode géophysique (0,25 points)

Justifiez le choix de la méthode TDEM pour caractériser la profondeur des eaux saumâtres par rapport aux méthodes FEM et de tomographie de résistivité électrique dans le cadre d'une étude régionale en Montérégie.

<span style="color:red">
Réponse:

</span>

### Étape 4: Acquisition des données (1,25 points)

Les données qui ont été acquises ont été jugées de mauvaise qualité. On vous demande ici de procéder au contrôle de qualité afin de vérifier cette affirmation.


__A)__ &nbsp;  Sur la même figure, tracez les courbes $\large \frac{\partial B_z}{\partial t} $ (en $\small nV/m^2$) des données contenues dans `données_brutes.npy` en fonction des 600 stations de mesures. Vous utiliserez la fonction semilogy pour la représentation. Le fichier `donnees_HauteTension.npy` contient une mesure fournie par la compagnie d'acquisition indiquant la proximité des lignes haute-tension pour chaque station de mesure. À l'aide de celle-ci, identifiez et délimitez les sondages affectés par les lignes hautes tensions. Identifier la zone affectée à l'aide de rectangles sur la figure des données brutes. <br> <br>

In [ ]:
#Charger les données nécessaires

DonneesBrutes = np.load("donnees_brutes.npy")
DistanceLigne = np.load("donnees_HauteTension.npy")
viridis = plt.cm.get_cmap('viridis')

# Vérifier la dimension des données
print("Dimension des données: ",DonneesBrutes.shape)
print("Dimension des données sur la distance des lignes hautes tensions: ",DistanceLigne.shape)

# Afficher les données

fig, ax = plt.subplots(2,1, figsize=(10,6), sharex=True)

# Déplacez les rectangles pour identifier les données affectées par les lignes haute tension.

rect1 = patches.Rectangle((1, 100), 100, 10000, linewidth=2, edgecolor='r', facecolor='none', zorder=10)
rect2 = patches.Rectangle((500, 100), 100, 10000, linewidth=2, edgecolor='r', facecolor='none', zorder=10)
ax[0].add_patch(rect1)
ax[0].add_patch(rect2)

for station in range(1, DonneesBrutes.shape[0]):
    ax[0].semilogy(DonneesBrutes[station,:],color = viridis.colors[station*int(256/44)])
    
ax[0].set_yscale("log")
ax[0].set_ylabel(r"$\frac{\partial B_z}{\partial t} (nV/m^2)$")
ax[1].set_xlabel("Station")
ax[1].plot(DistanceLigne)
ax[1].set_ylabel("Indication de la \ndistance des lignes")
plt.suptitle('Figure 1 : Représentation des données brutes', fontsize = 13)



plt.show()

<span style="color:red">
Réponse:

</span>

<br>
<p style="line-height:1.7 ; text-align: justify ">
<b>B)</b> &nbsp; Choisissez deux stations de sondage, l’une affectée par les lignes de haute tension et l’autre non affectée. Ensuite, représentez les courbes $\large \frac{\partial B_z}{\partial t} $ <br> (en $\small nV/m^2$) de ces deux sondages en fonction des temps d’enregistrement de la variable <code>GATE_V.npy</code> en ms. Vous utiliserez la fonction loglog. </p> <br>

In [ ]:
# Charger les données:
GateV = np.load("GATE_V.npy")

StAffect = #... inscrire le no de la station affectée par les lignes haute tension
StNonAffect = #... inscrire le no de la station non-affectée par les lignes haute tension

fig, ax = plt.subplots(1,1, figsize=(10,3.5))
ax.loglog(GateV[:,0], DonneesBrutes[:, StAffect], label="Sondage bruité")
ax.loglog(GateV[:,0], DonneesBrutes[:, StNonAffect], label="Sondage non bruité")
ax.legend(loc="best")
ax.set_xlabel('Temps (ms)')
ax.set_ylabel(r'$ \dfrac{\partial B_z}{\partial t}  \; \; [nV/m^2]$', fontsize=11)
plt.suptitle('Figure 2 : Comparaison des mesures bruités et non bruités', fontsize = 13)
plt.show()

<br>

__C)__ &nbsp; Que remarquez-vous? Selon vous, quel mode de représentation est le plus adapté
pour identifier les sondages affectés par les lignes de haute tension?

<span style="color:red">
Réponse : 

</span>

### Étape 5 Traitement des données (7 points)

Comme les données acquises ne sont pas de bonne qualité, vous ne les traiterez pas dans ce laboratoire. On vous demande plutôt de faire une inversion sur des données synthétiques afin d'identifier le meilleur système pour faire des mesures ultérieures.

Une analyse sur des données synthétiques est souvent utilisée afin de vérifier qu'une méthode géophysique, une méthode d'inversion ou un levé prévu peuvent bien atteindre les objectifs visés. Par exemple, on procédera à une analyse synthétique pour déterminer si les paramètres d'acquisition d'un levé TDEM peuvent bien atteindre une cible à une profondeur X, ou bien que l'inversion des données permettent de bien résoudre un objet d'une taille X à une profondeur Y. 

La méthodologie générale est la suivante:

1. Construire un modèle conceptuel du site d'études, incluant les propriétés géophysiques attendues. On appelle ce modèle le modèle vrai.
2. Modéliser les données acquises avec la configuration des appareils qui seraient utilisées sur le terrain. Ce sont les données synthétiques. On considère par la suite les données synthétiques comme les vraies données acquises sur le terrain. 
3. Appliquer le traitement prévu sur les données synthétiques. 
4. Varier les paramètres d'acquisition ou du traitement afin de voir l'impact sur le résultat final.
5. Identifier les paramètres optimaux pour atteindre les objectifs du levé et juger de la fiabilité des mesures.


__A)__ &nbsp; Le modèle vrai vous est fourni dans les fichiers `EP.npy` et `RES.npy`, respectivement donnant les épaisseurs et les résistivités des couches pour chaque station.  Il comporte 4 couches d’épaisseurs variables suivant la stratigraphie présentée au tableau 1. On vous demande de mettre en graphique le modèle vrai à l’aide de la fonction `plot_couches`. Bien identifier les axes et inclure une barre de couleur.

In [ ]:
def plot_couches(ax, res, ep, eplast=10):
    """
    ax:  L'axe sur lequel afficher la figure
    res: vecteur contenant les résistivités
    ep: Vecteur contenant les épaisseurs des couches
    eplast: Si l'épaisseur de la dernière couche n'est pas donnée, 
            donne une épaisseur eplast par défaut
    """
    if res.shape[0]-1 == ep.shape[0]:
        ep = np.concatenate([ep, np.full((1, ep.shape[1]), eplast)], axis=0)
    X = np.tile(np.arange(0.5, ep.shape[1]+1), (ep.shape[0]+1, 1))
    Y = np.concatenate((np.zeros((1, ep.shape[1])), np.cumsum(ep,axis = 0)), axis = 0)
    Y = np.hstack((Y, Y[:,-1].reshape(-1,1)))
    Z=res
    c = ax.pcolor(X, Y, Z, vmin=0, vmax=100, shading="flat")
    ax.invert_yaxis()
    ax.set_ylim(top=0, bottom=140)
    plt.colorbar(c, ax=ax,label = r'Résistivité $\rho (\Omega m)$')

In [ ]:
Ep = np.load('EP.npy')
Res = np.load('RES.npy')

In [ ]:
#Mettre en graphique le modèle vrai avec la fonction plot_couches

<br>

<p style="line-height:1.7 ; text-align: justify ">
<b> B) </b> &nbsp; Afin de modéliser les mesures avec les deux systèmes à l'étude, le NanoTEM et le VTEM, il faut spécifier la forme du courant au transmetteur. Ces deux systèmes utilisent des courants ainsi que des fenêtres de temps de mesure différents. Le signal du courant est contenu dans les variables <code>WAVE_N</code> (NanoTEM) et <code>WAVE_V</code> (VTEM), pour lesquels la première rangée est le temps en ms et la deuxième le courant en ampères. Les fenêtres de mesure sont contenues dans les variables <code>GATE_N</code> (NanoTEM) et <code>GATE_V</code> (VTEM), où la première colonne indique le centre de la fenêtre de mesure (en ms) et la deuxième la largeur. Produisez des figures montrant les signaux du transmetteur et des figures montrant le centre des fenêtres de temps en fonction de la mesure.
</p>

In [ ]:
# Charger les données

WaveN = np.load('WAVE_N.npy')
WaveV = np.load('Wave_V.npy')
GateN = np.load('GATE_N.npy')
GateV = np.load('GATE_V.npy')

In [ ]:
fig, axs = plt.subplots(2,2, figsize=(10,7))


# Afficher le signal du courant

axs[0,0].plot(WaveN[:,0], WaveN[:,1])
axs[1,0].plot(WaveV[:,0], WaveV[:,1])


# Afficher le centre de la fenêtre de mesure et leur largeur

axs[0,1].plot(np.arange(0, GateN.shape[0],1), GateN[:,0])
axs[0,1].errorbar(np.arange(0, GateN.shape[0], 1), GateN[:, 0], yerr=GateN[:, 1], linestyle="None", capsize=3)
axs[0,1].set_yscale("log")

axs[1,1].plot(np.arange(0, GateV.shape[0],1), GateV[:,0])
axs[1,1].errorbar(np.arange(0, GateV.shape[0], 1), GateV[:, 0], yerr=GateV[:, 1], linestyle="None", capsize=3)
axs[1,1].set_yscale("log")


# Définir les titres d'axes et de graphique

for ax in axs[:,0]:
    ax.set_ylabel("Courant (A)")
    ax.set_xlabel("Temps (ms)")
    
for ax in axs[:,1]:
    ax.set_ylabel("Centre de la fenêtre de mesure (ms)")
    ax.set_xlabel("Mesure")

axs[0,0].set_title("Signaux NanoTEM")
axs[1,0].set_title("Signaux VTEM")
axs[0,1].set_title("Centre des fenêtres de mesure NanoTEM")
axs[1,1].set_title("Centre des fenêtres de mesure VTEM")

plt.suptitle('Figure 4 : Courants et fenêtres de temps des mesures NanoTEM et VTEM', fontsize = 13)


plt.tight_layout()
plt.show()

<br>

<p style="font-size:15px">
Commentez sur les différences entre le NanoTEM et le VTEM pour le signal au transmetteur ainsi que pour les fenêtre d'écoute. En particulier, discutez de comment cela affectera la résolution pour les faibles profondeurs et la profondeur d'investigation.
</p>


<span style="color:red">
Réponse:
    
</span>

<br>

<p style="line-height:1.7 ; text-align: justify ">
&nbsp; En utilisant les fonctions <code>MODELISATION_VTEM.py</code> (VTEM-plus) et <code>MODELISATION_NanoTEM.py</code> (NanoTEM), modélisez les 40 courbes de sondages acquises avec le système hélicoporté (VTEM) à une hauteur de 30m et au sol (NanoTEM). Ces données sont les mesures de $\large \frac{\partial B_z}{\partial t} $ en nV/m2 . Ceci consistera en vos données synthétiques.
</p>

In [ ]:
# Vous pouvez utiliser la fonction help() pour obtenir une description des fonctions

help(Modelisation_NanoTEM)
help(Modelisation_VTEM)

# Initialiser les vecteurs qui vont contenir la réponse

dBzNano = np.zeros((GateN.shape[0], 40))
dBzVTEM = np.zeros((GateV.shape[0], 40))

for i in range(40):
    dBzNano[:,i] = Modelisation_NanoTEM(WaveN, GateN, Res[:, i], Ep[:, i])
    dBzVTEM[:,i] = Modelisation_VTEM(WaveV, GateV, 30, Res[:, i], Ep[:, i])

<br>

<b> C) </b>  &nbsp; Avec les fonctions semilogy et subplots, représentez les courbes $\large \frac{\partial B_z}{\partial t} $ modélisées comme à l'étape 4<b>a</b>. 


In [ ]:
fig, ax = plt.subplots(2,1, figsize=(10,8), sharex=True)

# Afficher les résultats

plt.tight_layout()
plt.show()

<br>

<p style="line-height:1.7 ; text-align: justify ">
Comparez l’intensité en $\small nV/m^2$ des courbes $\large \frac{\partial B_z}{\partial t} $ des deux systèmes. Que remarquez-vous et pourquoi?  </p>

<span style="color:red">
Réponse:
    
</span>


<b> D) </b>   &nbsp; On vous demande d'inverser manuellement une courbe de sondage avec un modèle à quatre couches. Ceci correspond à la courbe $\dfrac{\partial B_z}{\partial t}$ pour une station. Vous devez faire varier les résistivités dans <code>Res10</code> et les épaisseurs dans <code>Ep10</code>. Observez l'effet de chacun des paramètres sur la réponse et l'erreur rms et commentez sur la sensibilité de la courbe à chaque paramètre. N'oubliez pas que vous connaissez le modèle vrai.

In [ ]:
Res10 = np.array([40, 5, 150, 15]).reshape(-1,1) # Changez les résistivités des quatre couches ici
Ep10 = np.array([15, 20, 60, 20]).reshape(-1,1)  # Changez les épaisseurs des quatre couches ici

dBzV10 = Modelisation_VTEM(WaveV, GateV, 30, Res10[:,0], Ep10[:,0]) # Modéliser la réponse VTEM

rms10 = np.sqrt(np.sum((np.abs(dBzV10-dBzVTEM[:,9])/dBzV10)**2)/dBzV10.shape[0])*100 # Calculer l'erreur RMSE en &

fig, axs = plt.subplots(1,2, figsize=(10,5))

axs[0].loglog(GateV[:,0], dBzV10, label="Courbe modélisée")
axs[0].loglog(GateV[:,0], dBzVTEM[:,9], label="Courbe mesurée")
axs[0].legend(loc="best")
axs[0].annotate(f"rmse:{rms10:.2f} %", xycoords="axes fraction", xy=(0.02,0.2))
axs[0].set_title("Courbes modélisée et mesurée pour la station 10")
axs[0].set_ylabel(r'$ \dfrac{\partial B_z}{\partial t}  \; \; [nV/m^2]$', fontsize=11)
axs[0].set_xlabel('Temps (ms)')


plot_couches(axs[1], Res10, Ep10)
axs[1].set_xticks([])
axs[1].set_ylabel("Profondeur (m)")
axs[1].set_title("Modèle 1D")

fig.suptitle("Figure x: Inversion manuelle d'une courbe de sondage", fontsize = 13)

plt.show()

<span style="color:red">
Réponse:

</span>

<p style="line-height:1.7 ; text-align: justify ">
<b> E) </b> &nbsp; À la question précédente, vous avez inverser manuellement une seule courbe de sondage. La routine d'inversion permet de réaliser cette tâche de façon automatique pour chaque station. La combinaison des modèles 1D pour chaque station permet de retrouver un modèle 2D de propriétés. On vous demande donc maintenant d'inverser les données synthétiques pour les deux systèmes. Pour faire l'inversion, on doit choisir un modèle initial. Dans un premier temps,  utilisez le premier modèle initial contenu dans <code>modele_initial1.mat</code>. Ce modèle initial comprend 10 couches.
    
Utilisez les fonctions <code>INVERSION_VTEM.py</code> et <code>INVERSION_NanoTEM.py</code> pour procéder à l’inversion. Ces fonctions retournent les valeurs de sondage suite à l'inversion, la résistivité, la profondeur des couches et l'erreur rms. Stocker les dans des variables nommées seront <code>DATAinvVTEM1</code>, <code>Res1_V</code>, <code>Prof1_V</code>, <code>Ep1_V</code>,<code>Rms1_V</code>, <code>DATAinvNano1</code>, <code>Res1_N</code>, <code>Prof1_N</code>, <code>Ep1_N</code> et <code>Rms1_N</code>. </p>

In [ ]:
ModeleIni1 = np.load('modele_initial1.npy')
Ncouche = ModeleIni1.shape[0]

# Initialisation des sorties VTEM
DATAinvVTEM1= np.zeros((GateV.shape[0], 40))
Res1_V = np.zeros((Ncouche, 40))
Prof1_V = np.zeros((Ncouche-1, 40))
Ep1_V = np.zeros((Ncouche-1, 40))
Rms1_V = np.zeros((40, 1))

In [ ]:
#Écrire la boucle d'inversion pour le VTEM

for i in range(40):
    [DATAinvVTEM1[:,i], Res1_V[:,i], Prof1_V[:,i], Ep1_V[:,i], Rms1_V[i]] = Inversion_VTEM(dBzVTEM[:,i], # courbe 
                                                                            WaveV, # Signal VTEM
                                                                            GateV, # Fenêtres de mesure
                                                                            30,  # hauteur de vol
                                                                            ModeleIni1[:,0], # Resistivité initiale
                                                                            ModeleIni1[:,1]) # Épaisseur initiale
    print("Courbe", i+1,"/40 inversée.")
    

In [ ]:
# Initialisation des sorties NanoTEM
DATAinvNano1 = np.zeros((GateN.shape[0], 40))
Res1_N = np.zeros((Ncouche, 40))
Prof1_N = np.zeros((Ncouche-1, 40))
Ep1_N = np.zeros((Ncouche-1, 40))
Rms1_N = np.zeros((40, 1))

In [ ]:
#Écrire la boucle d'inversion pour le NanoTEM. Attention, les arguments ne sont pas exactement les mêmes.
help(Inversion_NanoTEM)

L'inversion prend un certain temps à rouler. Afin de vous faciliter la tache si vous avez à retravailler votre notebook, vous pouvez sauvegarder votre inversion.

In [ ]:
np.savez('ResultInv1_V', DATAinvVTEM1, Res1_V, Prof1_V, Ep1_V, Rms1_V)
np.savez('ResultInv1_N', DATAinvNano1, Res1_N, Prof1_N, Ep1_N, Rms1_N)

On peut ensuite lire les fichiers sauvegardés.

In [ ]:
ModeleIni1 = np.load('modele_initial1.npy')
ResultInv1_V = np.load('ResultInv1_V.npz')
ResultInv1_N = np.load('ResultInv1_N.npz')

DATAinvVTEM1 = ResultInv1_V['arr_0']
Res1_V = ResultInv1_V['arr_1']
Prof1_V = ResultInv1_V['arr_2']
Ep1_V = ResultInv1_V['arr_3']
Rms1_V = ResultInv1_V['arr_4']

DATAinvNano1 = ResultInv1_N['arr_0']
Res1_N = ResultInv1_N['arr_1']
Prof1_N = ResultInv1_N['arr_2']
Ep1_N = ResultInv1_N['arr_3']
Rms1_N = ResultInv1_N['arr_4']

<br>

<b> F) </b> &nbsp; Sur une même figure avec la fonction subplot, représentez les modèles électriques (sections 2D) initial et après inversion.

In [ ]:
#Répondre ici.

fig, axs = plt.subplots(2,2, figsize = (20,12))

# Modèle vrai


# Modèle initial
plot_couches(axs[0,1], 
             np.tile(ModeleIni1[:, 0].reshape(-1, 1), [1, Ep.shape[1]]),
             np.tile(ModeleIni1[:, 1].reshape(-1, 1), [1, Ep.shape[1]]))
axs[0][1].set_xlabel('Station \n')
axs[0][1].set_ylabel('Profondeur (m)')
axs[0][1].set_title('Modèle initial')

# Modèle inverse VTEM


# # Modèle inverse NanoTEM


plt.suptitle("Figure 6 : Résulat de l'inversion à 10 couches", fontsize = 15)
plt.show()

Comment se comparent les deux modèles inversés par rapport au modèle vrai ? Est-ce cohérent avec votre analyse des courants et fenêtres d'écoute pour les deux systèmes ?

<span style="color:red">
Réponse:

</span>

<br>

<b> G) </b> &nbsp;  Faites une figure montrant les données modélisées et inversées pour le VTEM sur un graphique, et la NanoTEM sur un autre graphique pour la station 20. Vous pouvez vous inspirer de l'étape 4B) pour le code.

In [ ]:
# Affichez les résultats.

<b> H) </b> &nbsp;  Affichez les valeurs RMSE en pourcentage retourné par l’inversion pour chaque station.

In [ ]:
#Répondre ici.

<b> I) </b> &nbsp; Est-ce que les données sont bien reproduites par les modèles inversés ? Justifiez votre réponse à l'aide des deux graphiques précédents.

<span style="color:red">
Réponse:

</span>

<br>

<b> J) </b> &nbsp;  Refaites l'inversion avec le deuxième modèle initial <code>modele_initial2.mat</code>. Ce dernier ne comprend que 4 couches. 

Stocker les dans des variables nommées <code>DATAinvVTEM2</code>, <code>RES2_V</code>, <code>PROF2_V</code>, <code>RMS2_V</code>, <code>DATAinvNano2</code>, <code>RES2_N</code>, <code>PROF2_N</code> et <code>RMS2_N</code>. </p>

In [ ]:
ModeleIni2 = np.load('modele_initial2.npy')
Npar = ModeleIni2.shape[0]

# Initialisation des sorties VTEM
DATAinvVTEM2 = np.zeros((GateV.shape[0], 40))
Res2_V = np.zeros((Npar, 40))
Prof2_V = np.zeros((Npar-1, 40))
Ep2_V = np.zeros((Npar-1, 40))
Rms2_V = np.zeros((40, 1))

In [ ]:
#Écrire la boucle d'inversion pour le VTEM

In [ ]:
# Initialisation des sorties NanoTEM
DATAinvNano2 = np.zeros((GateN.shape[0], 40))
Res2_N = np.zeros((Npar, 40))
Prof2_N = np.zeros((Npar-1, 40))
Ep2_N = np.zeros((Npar-1, 40))
Rms2_N = np.zeros((40, 1))

In [ ]:
#Écrire la boucle d'inversion pour le NanoTEM

In [ ]:
# Sauvegarde données inversion

np.savez('ResultInv2_V', DATAinvVTEM2, Res2_V, Prof2_V, Ep2_V, Rms2_V)
np.savez('ResultInv2_N', DATAinvNano2, Res2_N, Prof2_N, Ep2_N, Rms2_N)

In [ ]:
# Charger données de l'inversion
ModeleIni2 = np.load('modele_initial2.npy')
ResultInv2_V = np.load('ResultInv2_V.npz')
ResultInv2_N = np.load('ResultInv2_N.npz')

DATAinvVTEM2 = ResultInv2_V['arr_0']
Res2_V = ResultInv2_V['arr_1']
Prof2_V = ResultInv2_V['arr_2']
Ep2_V = ResultInv2_V['arr_3']
Rms2_V = ResultInv2_V['arr_4']

DATAinvNano2 = ResultInv2_N['arr_0']
Res2_N = ResultInv2_N['arr_1']
Prof2_N = ResultInv2_N['arr_2']
Ep2_N = ResultInv2_N['arr_3']
Rms2_N = ResultInv2_N['arr_4']

<br>

<b> K) </b> &nbsp; Sur une même figure avec la fonction subplot, représentez les modèles électriques (sections 2D) initial et après inversion.

In [ ]:
#Répondre ici.

<br>

<b> L) </b> &nbsp;  Affichez les données modélisées et inversées pour le VTEM sur un axe, et le NanoTEM sur un autre axe pour la station 20.

In [ ]:
#Répondre ici.

<b> M) </b> &nbsp;  Affichez les valeurs RMSE en pourcentage retournées par l’inversion pour chaque station.

In [ ]:
#Répondre ici.

<b> N) </b> &nbsp; Est-ce que les données sont bien reproduites par les modèles inversés ? Est-ce que l'ajustement des données est meilleurs qu'avec le modèle à 10 couches ?

<span style="color:red">
Réponse:
 
</span>

### Étape 6 Interprétation des données (0,5 points)

Discutez de l’influence du modèle initial sur l’inversion. Sans aucune information sur la géologie, quel modèle utiliseriez-vous ? </p>

<span style="color:red">
Réponse:

</span>

### Étape 7 Synthèse (0,5 points)
Déterminer quel système entre le NanoTEM et le VTEM est le plus approprié pour détecter le toit de la zone d’eaux saumâtres.

<span style="color:red">
Réponse:
    
</span>
